# Trainiertes Modell auf RCP2.6 Daten anwenden

In diesem Notebook wird das Modell, das auf den vergangenen Niederschlags-, Temperatur- und Abflussdaten trainiert wurde, auf die Temperatur- und Niederschlagsdaten unter RCP2.6 angewendet. Dabei wird der in den historischen Daten erlernte Zusammenhang genutzt, um auf Basis der neuen Temperatur- und Niederschlagswerte den zukünftigen Abfluss zu prognostizieren. Die Ergebnisse werden abschließend in einer CSV-Datei gespeichert.

In [2]:
# Bibliotheken laden
import pandas as pd
import numpy as np
from tensorflow.keras.models import load_model
from sklearn.preprocessing import StandardScaler
import joblib 
import os

work_dir = "/Users/emmamorlock/git/GitHub/projektstudie-murgtal"  
os.chdir(work_dir)

# Bias-korrigierte Niederschlags- und Temperaturdaten unter RCP2.6 laden
df_rcp26 = pd.read_csv("data/future_bias_corrected_rcp26.csv", parse_dates=["date"])

In [4]:
# Übersicht über df_rcp85 anzeigen lassen
df_rcp26.describe()

t2m_mean        tp_sum
count  34698.000000  34698.000000
mean       8.668877      4.103913
std        7.295344      7.525990
min      -19.128577      0.000000
25%        3.121408      0.000000
50%        8.721414      0.400819
75%       14.354745      5.315207
max       27.271402    113.222627

In [5]:
import pandas as pd
import joblib
from tensorflow.keras.models import load_model
!pip install tqdm
from tqdm import trange

# Modell & Scaler laden
model = load_model("data/model_lag3.keras")
x_scaler = joblib.load("data/x_scaler.pkl")
y_scaler = joblib.load("data/y_scaler.pkl")

# RCP-Daten laden
df_rcp26 = pd.read_csv("data/future_bias_corrected_rcp26.csv", parse_dates=["date"])

# Initiale Werte
flow_values = [16, 16, 16]

# Feature-Reihenfolge wie beim Training
feature_order = [
    "t2m_mean", "tp_sum",
    "tas_lag_1", "prec_lag_1", "flow_lag_1",
    "tas_lag_2", "prec_lag_2", "flow_lag_2",
    "tas_lag_3", "prec_lag_3", "flow_lag_3"
]

# Neue Datei anlegen und Header schreiben
with open("data/rcp26_flow_predicted.csv", "w") as f:
    f.write("date,t2m_mean,tp_sum,predicted_flow_m3_s\n")

# Iteration & direktes Schreiben
for i in trange(3, len(df_rcp26), desc="Berechne Vorhersagen"):
    X_input = {
        "t2m_mean": df_rcp26.loc[i, "t2m_mean"],
        "tp_sum": df_rcp26.loc[i, "tp_sum"],

        "tas_lag_1": df_rcp26.loc[i - 1, "t2m_mean"],
        "tas_lag_2": df_rcp26.loc[i - 2, "t2m_mean"],
        "tas_lag_3": df_rcp26.loc[i - 3, "t2m_mean"],

        "prec_lag_1": df_rcp26.loc[i - 1, "tp_sum"],
        "prec_lag_2": df_rcp26.loc[i - 2, "tp_sum"],
        "prec_lag_3": df_rcp26.loc[i - 3, "tp_sum"],

        "flow_lag_1": flow_values[-1],
        "flow_lag_2": flow_values[-2],
        "flow_lag_3": flow_values[-3],
    }

    x_df = pd.DataFrame([X_input])[feature_order]
    x_scaled = x_scaler.transform(x_df)
    y_scaled = model.predict(x_scaled)
    y_pred = y_scaler.inverse_transform(y_scaled).flatten()[0]

    flow_values.append(y_pred)

    # Direkt in Datei schreiben
    with open("data/rcp26_flow_predicted.csv", "a") as f:
        f.write(f"{df_rcp26.loc[i, 'date']},{df_rcp26.loc[i, 't2m_mean']},{df_rcp26.loc[i, 'tp_sum']},{y_pred}\n")


Berechne Vorhersagen:   0%|                           | 0/34695 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step


Berechne Vorhersagen:   0%|                 | 1/34695 [00:00<1:25:38,  6.75it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step


Berechne Vorhersagen:   0%|                   | 4/34695 [00:00<33:30, 17.26it/s]

...

Berechne Vorhersagen: 100%|██████████████▉| 34689/34695 [21:13<00:00, 25.98it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step


Berechne Vorhersagen: 100%|██████████████▉| 34692/34695 [21:13<00:00, 25.79it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step


Berechne Vorhersagen: 100%|███████████████| 34695/34695 [21:13<00:00, 27.24it/s]
